## Entrenchment analysis

In [1]:
import pandas as pd 
import altair as alt 
import numpy as np
import scipy
import theme

alt.themes.register('main_theme', theme.main_theme)
alt.themes.enable('main_theme')

alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
phenotypes_df = pd.read_csv('results/h3n2_ha_60y_phenotypes_df.csv')

site_map = pd.read_csv('../data/site_numbering_map.csv')

phenotypes_df = pd.merge(
    phenotypes_df,
    site_map,
    left_on=['site', 'sequential_site', 'wildtype', 'region'], 
    right_on=['reference_site', 'sequential_site', 'sequential_wt', 'region'], 
).drop(
    columns=['sequential_site', 'reference_site', 'sequential_wt']
).assign(
    appeared=phenotypes_df['most_recent_fix_date'].notna(),
    stability_measured=phenotypes_df['pH stability'].notna(),
    in_rbs=lambda x: x['rbs_region'].apply(
        lambda r: "Inside receptor binding pocket" if r != "outside RBS" else "Outside receptor binding pocket"
    )
)

In [3]:
def plot_phenotype_vs_date(data, phenotype, phenotype_title, colors):
    rbs_colors = {
        "Inside receptor binding pocket": colors[0],
        "Outside receptor binding pocket": colors[1],
    }

    y_min = data[phenotype].min()
    y_max = data[phenotype].max()

    x_min = pd.to_datetime(data['most_recent_fix_date']).min()
    x_max = pd.to_datetime(data['most_recent_fix_date']).max()

    # Ensure date is in datetime format
    data['most_recent_fix_date'] = pd.to_datetime(data['most_recent_fix_date'])

    # sort data to control which points overlay others
    data = data.sort_values('site', ascending=False)

    # Create base chart without data specification
    base = alt.Chart().encode(
        x=alt.X(
            "most_recent_fix_date:T",
            title=(["Most recent date when", "amino acid was fixed"]),
            scale=alt.Scale(
                domain=[x_min, x_max]
            )
        ),
        y=alt.Y(
            phenotype,
            title=phenotype_title,
            scale=alt.Scale(
                domain=[y_min, y_max]
            )
        ),
        color=alt.Color(
            "in_rbs",
            scale=alt.Scale(domain=list(rbs_colors.keys()), range=list(rbs_colors.values())),
            title=None,
            legend=None
        ),
        tooltip=[
            'site', 'wildtype', 'mutant', 'region', 'max_frequency', phenotype,
            'pH stability', 'rbs_region', 'most_recent_fix_date'
        ]
    )

    # Create horizontal line specification
    hline = alt.Chart().mark_rule(
        color='black',
        size=1.25,
        opacity=1.0,
        strokeDash=[6,6]
    ).encode(y=alt.Y(datum=0))

    # Layer everything together first
    complete_layer = alt.layer(
        base.mark_circle(size=60, opacity=1, stroke='black', strokeWidth=0.5),  # scatter plot
        hline,
        base.transform_regression(
            'most_recent_fix_date',
            phenotype,
            groupby=['in_rbs'],
        ).mark_line(size=3),
    ).properties(
        width=300,
        height=150
    )

    # Apply faceting with data specification
    complete_chart = complete_layer.facet(
        data=data.query('mutant != wildtype and most_recent_fix_date.notna()'),
        facet=alt.Facet(
            'in_rbs',
            title=None,
            header=alt.Header(
                labelFontSize=16,
                labelFontWeight='bold',
            )
        ),
        columns=1
    ).resolve_scale(
        y='independent',
        x='independent'
    )

    return complete_chart

In [4]:
entry_chart = plot_phenotype_vs_date(
    phenotypes_df, 
    'MDCKSIAT1 cell entry', 
    ['Effect on cell entry in', 'MA22 background'],
    ['#E41A1C', '#FFC1C3']
) 

stability_chart = plot_phenotype_vs_date(
    phenotypes_df, 
    'pH stability', 
    ['Effect on stability in', 'MA22 background'],
    ['#377EB8', '#C6DBEF']
) 

(entry_chart | stability_chart).resolve_scale(color='independent')

alt.HConcatChart(...)

In [5]:
entry_chart

alt.FacetChart(...)

In [6]:
stability_chart

alt.FacetChart(...)

In [7]:
from scipy.stats import linregress

def get_fractional_year(dt):
    yr_start = pd.Timestamp(year=dt.year, month=1, day=1)
    nxt_yr_start = pd.Timestamp(year=dt.year + 1, month=1, day=1)
    return dt.year + ((dt - yr_start) / (nxt_yr_start - yr_start))

# get slope of the linear regression for cell entry in receptor binding pocket
regress_df = phenotypes_df.query(
    'mutant != wildtype and most_recent_fix_date.notna()'
).query(
    'in_rbs == "Inside receptor binding pocket"'
)[['MDCKSIAT1 cell entry', 'most_recent_fix_date']]

# convert datetime to numeric format
regress_df['year'] = regress_df['most_recent_fix_date'].apply(get_fractional_year)

slope, intercept, r_value, p_value, std_err = linregress(
    regress_df['year'], regress_df['MDCKSIAT1 cell entry']
)

print("Slope (change in cell entry per year): ", slope)

Slope (change in cell entry per year):  -0.014441403007993986


In [23]:
frequencies_df = pd.read_csv('results/h3n2_ha_60y_frequencies_df.csv')

def detect_reversion(group):
    group = group.sort_values('timepoint')
    allele_sequence = group.loc[group['frequency'] > 0.95, 'allele'].tolist()

    # check if any allele reappears after disappearing
    seen = []
    curr_allele = allele_sequence[0]
    for allele in allele_sequence:
        if allele != curr_allele and allele in seen:
            return True
        if allele not in seen:
            seen.append(allele)
        curr_allele = allele
    return False

def classify_sweep(group):
    fixed_aa = group.query('frequency >= 0.95')
    if len(fixed_aa['allele'].unique()) == 1:
        return 'conserved'
    elif len(fixed_aa['allele'].unique()) == 2 and detect_reversion(group) is False:
        return 'single sweep'
    elif len(fixed_aa['allele'].unique()) > 2 and detect_reversion(group) is False:
        return 'multiple sweep'
    elif detect_reversion(group) is True:
        return 'reversion'
    else:
        return None

sweep_classifications = frequencies_df.groupby('site').apply(classify_sweep)

sweep_category = frequencies_df.assign(
    sweep_type=frequencies_df['site'].map(sweep_classifications)
)[['site', 'sweep_type']].drop_duplicates().reset_index(drop=True)

sweep_category

site      sweep_type
0       1       conserved
1       2  multiple sweep
2       3       reversion
3       4       conserved
4       5       conserved
..    ...             ...
545   546       conserved
546   547       conserved
547   548       conserved
548   549       conserved
549   550       conserved

[550 rows x 2 columns]

In [24]:
phenotypes_and_sweeps = pd.merge(
    phenotypes_df,
    sweep_category,
    on=['site']
)

In [49]:
np.sort(phenotypes_and_sweeps.query('sweep_type == "reversion"')['site'].unique())

array([  3,  83, 124, 131, 133, 142, 145, 155, 156, 159, 160, 172, 189,
       193, 197, 217, 225, 375, 450])

In [35]:
import polyclonal

In [51]:
polyclonal.plot.lineplot_and_heatmap(
    data_df=phenotypes_and_sweeps.assign(dummy_category=1),
    stat_col='MDCKSIAT1 cell entry',
    category_col='dummy_category',
    alphabet=polyclonal.alphabets.biochem_order_aas(polyclonal.alphabets.AAS_WITHSTOP),
    init_floor_at_zero=False,
    sites=np.sort(phenotypes_and_sweeps.query(
        'sweep_type == "reversion" and in_rbs == "Outside receptor binding pocket"'
    )['site'].unique()),
    show_lineplot=False,
    show_zoombar=False,
)

alt.VConcatChart(...)

In [52]:
polyclonal.plot.lineplot_and_heatmap(
    data_df=phenotypes_and_sweeps.assign(dummy_category=1),
    stat_col='MDCKSIAT1 cell entry',
    category_col='dummy_category',
    alphabet=polyclonal.alphabets.biochem_order_aas(polyclonal.alphabets.AAS_WITHSTOP),
    init_floor_at_zero=False,
    sites=np.sort(phenotypes_and_sweeps.query(
        'sweep_type == "reversion" and in_rbs == "Inside receptor binding pocket"'
    )['site'].unique()),
    show_lineplot=False,
    show_zoombar=False,
)

alt.VConcatChart(...)

In [31]:
# Base density chart
alt.Chart(
    phenotypes_and_sweeps.query(
        'mutant != wildtype'
    )
).transform_density(
    density='MDCKSIAT1 cell entry',
    bandwidth=0.3,
    groupby=['sweep_type', 'in_rbs'],
    extent=[-5, 1],
    counts=True,
    steps=200
).mark_area(
    fillOpacity=0.6,
    stroke='black'
).encode(
    x=alt.X('value:Q', title='MDCKSIAT1 cell entry'),
    y=alt.Y('density:Q',
           stack='zero',
           title=None),
    color=alt.Color('sweep_type:N', legend=None)
).properties(
    height=60,
    width=200
).facet(
    row=alt.Row('sweep_type:N', title=None),
    column=alt.Column('in_rbs:N', title=None)
).resolve_scale(
    y='independent'
)

alt.FacetChart(...)

In [26]:
alt.Chart(
    phenotypes_and_sweeps.query('sweep_type == "conserved"').query('in_rbs == "Outside receptor binding pocket"')
).mark_rect(opacity=0.9, stroke='black', strokeWidth=0.3).encode(
    x=alt.X(
        'site:O', 
        sort=alt.SortField(field='site')
    ),
    y='mutant',
    color=alt.Color(
        'MDCKSIAT1 cell entry', 
        scale=alt.Scale(scheme='redblue', domainMid=0),
    ),
    tooltip=['site', 'mutant', alt.Tooltip('MDCKSIAT1 cell entry', format='.2f')]
)

alt.Chart(...)

In [34]:
alt.Chart(
    phenotypes_and_sweeps.query('sweep_type == "reversion"')
).mark_rect(opacity=0.9, stroke='black', strokeWidth=0.3).encode(
    x=alt.X(
        'site:O', 
        sort=alt.SortField(field='site')
    ),
    y='mutant',
    color=alt.Color(
        'MDCKSIAT1 cell entry', 
        scale=alt.Scale(scheme='redblue', domainMid=0),
    ),
    tooltip=['site', 'mutant', alt.Tooltip('MDCKSIAT1 cell entry', format='.2f')]
).facet(
    column=alt.Column('in_rbs:N', title='In RBS', header=alt.Header(labelAngle=0))
).resolve_scale(
    x='independent'
)

alt.FacetChart(...)

In [30]:
phenotypes_and_sweeps

site wildtype mutant  MDCKSIAT1 cell entry  pH stability region  \
0        1        Q      A               -0.1226      0.004237    HA1   
1        1        Q      C               -0.5732     -0.014300    HA1   
2        1        Q      D                0.2550     -0.021900    HA1   
3        1        Q      E                0.2941      0.006890    HA1   
4        1        Q      F               -0.7141     -0.001402    HA1   
...    ...      ...    ...                   ...           ...    ...   
9486   499        R      T               -4.9650           NaN    HA2   
9487   499        R      V               -4.8280           NaN    HA2   
9488   499        R      W               -4.8530           NaN    HA2   
9489   499        R      Y               -4.8290           NaN    HA2   
9490   499        R      R                0.0000      0.000000    HA2   

      nt changes to codon allele  max_frequency  fix_frequency_cutoff  \
0                       2    NaN            NaN                   NaN   
1                       3    NaN            NaN                   NaN   
2                       2    NaN            NaN                   NaN   
3                       1    NaN            NaN                   NaN   
4                       3    NaN            NaN                   NaN   
...                   ...    ...            ...                   ...   
9486                    2    NaN            NaN                   NaN   
9487                    2    NaN            NaN                   NaN   
9488                    1    NaN            NaN                   NaN   
9489                    3    NaN            NaN                   NaN   
9490                    0      R            1.0                  0.95   

        most_recent_fix_date  most_recent_fix_frequency   rbs_region  \
0                        NaT                        NaN  outside RBS   
1                        NaT                        NaN  outside RBS   
2                        NaT                        NaN  outside RBS   
3                        NaT                        NaN  outside RBS   
4                        NaT                        NaN  outside RBS   
...                      ...                        ...          ...   
9486                     NaT                        NaN  outside RBS   
9487                     NaT                        NaN  outside RBS   
9488                     NaT                        NaN  outside RBS   
9489                     NaT                        NaN  outside RBS   
9490 2021-12-01 14:17:31.200                        1.0  outside RBS   

      appeared  stability_measured                           in_rbs sweep_type  
0        False                True  Outside receptor binding pocket  conserved  
1        False                True  Outside receptor binding pocket  conserved  
2        False                True  Outside receptor binding pocket  conserved  
3        False                True  Outside receptor binding pocket  conserved  
4        False                True  Outside receptor binding pocket  conserved  
...        ...                 ...                              ...        ...  
9486     False               False  Outside receptor binding pocket  conserved  
9487     False               False  Outside receptor binding pocket  conserved  
9488     False               False  Outside receptor binding pocket  conserved  
9489     False               False  Outside receptor binding pocket  conserved  
9490      True                True  Outside receptor binding pocket  conserved  

[9491 rows x 17 columns]